In [1]:
from nipype.interfaces.io import DataSink, SelectFiles, DataGrabber 
from nipype.interfaces.utility import IdentityInterface, Function    
from nipype.pipeline.engine import Node, Workflow, JoinNode, MapNode
from nipype.interfaces import fsl
from nipype.interfaces import brainsuite
from nipype.interfaces.io import SelectFiles, DataSink, DataGrabber
from shutil import copyfile
from pandas import Series
from glob import glob
from os.path import abspath, expanduser, join
from os import chdir, remove, getcwd
from nipype import config, logging
from datetime import date
today = str(date.today())
config.enable_debug_mode()

In [2]:
#Set variables
subject_list = ['02-T2', '06-T1', '07-T2','08-T1', '09-T2', '10-T1', '11-T1', '12-T1', '13-T1', '15-T1', '16-T1', '17-T1',
                '18-T1', '19-T1', '20-T1', '21-T1', '22-T1', '23-T1', '24-T1', '29-T1', '30-T1', '31-T1', '32-T1',
                '35-T1', '36-T1', '37-T1', '38-T1', '40-T1', '102-T1', '103-T1', '104-T1', '105-T1', '106-T1', '107-T1', '108-T1', '109-T1',
                '110-T1', '111-T1']

#subject_list = ['08-T1']#, '20-T1','22-T1','29-T1','31-T1','35-T1']

home = '/Volumes/group/proc/TIGERanalysis/qT1'
fpath = join(home, 'subjDir')
workflow_dir = join(home, 'workflow_qT1_FLUXRUN')
data_dir = join(home, 'DataDir_qT1_FLUXRUN')

In [3]:
#Setup Datasink, Infosource, Selectfiles

datasink = Node(DataSink(base_directory = data_dir),
                   name='datasink')

#Set infosource iterables
infosource = Node(IdentityInterface(fields=['subject_id']),
                  name="infosource")
infosource.iterables = [('subject_id', subject_list)]

#SelectFiles
template = dict(t1=fpath+'/{subject_id}/T1_acpc.nii.gz',
               qt1=fpath+'/{subject_id}/qt1_T1fit_final.nii.gz')

sf = Node(SelectFiles(template, 
                      base_directory = fpath),
          name = 'sf')


In [4]:
#Skullstrip T1w image
stripT1 = Node(fsl.BET(out_file = 'T1_acpc_bet.nii.gz'),
             name = 'stripT1')
# stripT1.inputs.inputMRIFile = '/Users/lucindasisk/Dropbox/SNAPLab/Data/TIGER-T1/TIGER_qT1/06-T1/raw/T1_acpc.nii.gz'
# stripT1.run()

In [5]:
reorient = Node(fsl.Reorient2Std(out_file = 'reoriented_qT1.nii.gz',
                              output_type = 'NIFTI_GZ'),
                    name = 'reorient')

In [6]:
#Register qT1 to T1w
register_qt1 = Node(fsl.FLIRT(out_file = 'registered_qT1.nii.gz',
                              output_type = 'NIFTI_GZ',
                              out_matrix_file = 'flirt_transform_qt1.mat'),
                    name = 'register_qt1')

In [7]:
#Extract voxel values from qT1 beneath overlaid mask - Left Uncinate
get_voxLUF = Node(fsl.ImageMeants(show_all = True,
                               out_file = 'ROI_voxel-contrasts_LeftUncinate.txt'),
               name = 'get_voxLUF')

In [8]:
#Extract voxel values from qT1 beneath overlaid mask - Left Uncinate
get_voxLCC = Node(fsl.ImageMeants(show_all = True,
                               out_file = 'ROI_voxel-contrasts_LeftCC.txt'),
               name = 'get_voxLCC')

In [9]:
# #Extract voxel values from qT1 beneath overlaid mask - Left dAcc MRS Voxel
# get_voxLMRS = Node(fsl.ImageMeants(show_all = True,
#                                out_file = 'ROI_voxel-contrasts_LeftdACC_Voxel.txt'),
#                name = 'get_voxLMRS')

In [10]:
#Extract voxel values from qT1 beneath overlaid mask - Right Uncinate
get_voxRUF = Node(fsl.ImageMeants(show_all = True,
                               out_file = 'ROI_voxel-contrasts_RightUncinate.txt'),
               name = 'get_voxRUF')

In [11]:
#Extract voxel values from qT1 beneath overlaid mask - Right Uncinate
get_voxRCC = Node(fsl.ImageMeants(show_all = True,
                               out_file = 'ROI_voxel-contrasts_RightCC.txt'),
               name = 'get_voxRCC')

In [12]:
# #Extract voxel values from qT1 beneath overlaid mask - Right dAcc MRS Voxel
# get_voxRMRS = Node(fsl.ImageMeants(show_all = True,
#                                out_file = 'ROI_voxel-contrasts_RightdACC_Voxel.txt'),
#                name = 'get_voxRMRS')

In [15]:
qt1proc_flow = Workflow(name = 'qt1proc_flow')
qt1proc_flow.connect([(infosource, sf, [('subject_id','subject_id')]),
                      (sf, stripT1, [('t1', 'in_file')]),
                      (stripT1, datasink, [('out_file', '1_check_alignment')]),
                      (sf, reorient, [('qt1', 'in_file')]),
                      (reorient, datasink, [('out_file','1_check_alignment.@par')]),
                      (reorient, register_qt1, [('out_file', 'in_file')]),
                      (stripT1, register_qt1, [('out_file', 'reference')]),
                      (register_qt1, datasink, [('out_file', '1_check_alignment.@par.@par')])
                     ])
qt1proc_flow.base_dir = workflow_dir
qt1proc_flow.write_graph(graph2use = 'flat')
preproc = qt1proc_flow.run('MultiProc', plugin_args={'n_procs': 4})

190330-23:56:36,817 nipype.workflow DEBUG:
	 (qt1proc_flow.infosource, qt1proc_flow.sf): No edge data
190330-23:56:36,818 nipype.workflow DEBUG:
	 (qt1proc_flow.infosource, qt1proc_flow.sf): new edge data: {'connect': [('subject_id', 'subject_id')]}
190330-23:56:36,819 nipype.workflow DEBUG:
	 (qt1proc_flow.sf, qt1proc_flow.stripT1): No edge data
190330-23:56:36,819 nipype.workflow DEBUG:
	 (qt1proc_flow.sf, qt1proc_flow.stripT1): new edge data: {'connect': [('t1', 'in_file')]}
190330-23:56:36,820 nipype.workflow DEBUG:
	 (qt1proc_flow.stripT1, qt1proc_flow.datasink): No edge data
190330-23:56:36,821 nipype.workflow DEBUG:
	 (qt1proc_flow.stripT1, qt1proc_flow.datasink): new edge data: {'connect': [('out_file', '1_check_alignment')]}
190330-23:56:36,822 nipype.workflow DEBUG:
	 (qt1proc_flow.sf, qt1proc_flow.reorient): No edge data
190330-23:56:36,823 nipype.workflow DEBUG:
	 (qt1proc_flow.sf, qt1proc_flow.reorient): new edge data: {'connect': [('qt1', 'in_file')]}
190330-23:56:36,823 

190330-23:56:39,49 nipype.workflow DEBUG:
	 Parameterization: paramstr=_subject_id_24-T1
190330-23:56:39,52 nipype.workflow DEBUG:
	 [Node] infosource - setting input subject_id = 29-T1
190330-23:56:39,53 nipype.workflow DEBUG:
	 Parameterization: paramstr=_subject_id_29-T1
190330-23:56:39,56 nipype.workflow DEBUG:
	 [Node] infosource - setting input subject_id = 30-T1
190330-23:56:39,56 nipype.workflow DEBUG:
	 Parameterization: paramstr=_subject_id_30-T1
190330-23:56:39,59 nipype.workflow DEBUG:
	 [Node] infosource - setting input subject_id = 31-T1
190330-23:56:39,60 nipype.workflow DEBUG:
	 Parameterization: paramstr=_subject_id_31-T1
190330-23:56:39,63 nipype.workflow DEBUG:
	 [Node] infosource - setting input subject_id = 32-T1
190330-23:56:39,64 nipype.workflow DEBUG:
	 Parameterization: paramstr=_subject_id_32-T1
190330-23:56:39,66 nipype.workflow DEBUG:
	 [Node] infosource - setting input subject_id = 35-T1
190330-23:56:39,67 nipype.workflow DEBUG:
	 Parameterization: paramstr

190330-23:56:39,166 nipype.workflow DEBUG:
	 Removed the identity node qt1proc_flow.infosource from the graph.
190330-23:56:39,167 nipype.workflow DEBUG:
	 [Node] sf - setting input subject_id = 20-T1
190330-23:56:39,168 nipype.workflow DEBUG:
	 Removed the identity node qt1proc_flow.infosource from the graph.
190330-23:56:39,168 nipype.workflow DEBUG:
	 [Node] sf - setting input subject_id = 19-T1
190330-23:56:39,169 nipype.workflow DEBUG:
	 Removed the identity node qt1proc_flow.infosource from the graph.
190330-23:56:39,170 nipype.workflow DEBUG:
	 [Node] sf - setting input subject_id = 18-T1
190330-23:56:39,171 nipype.workflow DEBUG:
	 Removed the identity node qt1proc_flow.infosource from the graph.
190330-23:56:39,172 nipype.workflow DEBUG:
	 [Node] sf - setting input subject_id = 17-T1
190330-23:56:39,172 nipype.workflow DEBUG:
	 Removed the identity node qt1proc_flow.infosource from the graph.
190330-23:56:39,173 nipype.workflow DEBUG:
	 [Node] sf - setting input subject_id = 1

190330-23:56:48,330 nipype.workflow DEBUG:
	 [Node] Up-to-date cache found for "qt1proc_flow.sf".
190330-23:56:48,331 nipype.workflow DEBUG:
	 Checking hash "qt1proc_flow.sf" locally: cached=True, updated=True.
190330-23:56:48,332 nipype.workflow DEBUG:
	 [MultiProc] Submitted task qt1proc_flow.sf (taskid=3).
190330-23:56:48,333 nipype.workflow DEBUG:
	 Allocating qt1proc_flow.sf ID=15 (0.20GB, 1 threads). Free: 28.00GB, 0 threads.
190330-23:56:48,334 nipype.workflow DEBUG:
	 Setting node inputs
190330-23:56:48,334 nipype.workflow INFO:
	 [Node] Setting-up "qt1proc_flow.sf" in "/Volumes/group/proc/TIGERanalysis/qT1/workflow_qT1_FLUXRUN/qt1proc_flow/_subject_id_109-T1/sf".
190330-23:56:48,414 nipype.workflow DEBUG:
	 [Node] Hashes: [('base_directory', '/Volumes/group/proc/TIGERanalysis/qT1/subjDir'), ('force_lists', False), ('raise_on_empty', True), ('sort_filelist', True), ('subject_id', '109-T1')], a03c5111d5ca0161aeebaca294d38580, /Volumes/group/proc/TIGERanalysis/qT1/workflow_qT1_FL

190330-23:56:56,334 nipype.workflow DEBUG:
	 Setting node inputs
190330-23:56:56,335 nipype.workflow DEBUG:
	 input: in_file
190330-23:56:56,336 nipype.workflow DEBUG:
	 results file: /Volumes/group/proc/TIGERanalysis/qT1/workflow_qT1_FLUXRUN/qt1proc_flow/_subject_id_111-T1/sf/result_sf.pklz
190330-23:56:56,336 nipype.utils DEBUG:
	 Loading pkl: /Volumes/group/proc/TIGERanalysis/qT1/workflow_qT1_FLUXRUN/qt1proc_flow/_subject_id_111-T1/sf/result_sf.pklz
190330-23:56:56,334 nipype.workflow INFO:
	 [Node] Setting-up "qt1proc_flow.reorient" in "/Volumes/group/proc/TIGERanalysis/qT1/workflow_qT1_FLUXRUN/qt1proc_flow/_subject_id_111-T1/reorient".
190330-23:56:56,339 nipype.workflow DEBUG:
	 [Node] Directory not found "/Volumes/group/proc/TIGERanalysis/qT1/workflow_qT1_FLUXRUN/qt1proc_flow/_subject_id_111-T1/reorient".
190330-23:56:56,344 nipype.utils DEBUG:
	 Removing contents of /Volumes/group/proc/TIGERanalysis/qT1/workflow_qT1_FLUXRUN/qt1proc_flow/_subject_id_111-T1/reorient
190330-23:56:

...

	 Aggregate: False
190331-00:25:33,531 nipype.utils DEBUG:
	 File: /Volumes/group/proc/TIGERanalysis/qT1/DataDir_qT1_FLUXRUN/1_check_alignment/_subject_id_07-T2/reoriented_qT1.nii.gz already exists, not overwriting, copy:1190331-00:25:34,109 nipype.workflow INFO:
	 [Node] Finished "qt1proc_flow.sf".

190331-00:25:34,114 nipype.interface DEBUG:
	 key: 1_check_alignment.@par.@par files: /Volumes/group/proc/TIGERanalysis/qT1/workflow_qT1_FLUXRUN/qt1proc_flow/_subject_id_07-T2/register_qt1/registered_qT1.nii.gz
190331-00:25:34,204 nipype.interface DEBUG:
	 copyfile: /Volumes/group/proc/TIGERanalysis/qT1/workflow_qT1_FLUXRUN/qt1proc_flow/_subject_id_07-T2/register_qt1/registered_qT1.nii.gz /Volumes/group/proc/TIGERanalysis/qT1/DataDir_qT1_FLUXRUN/1_check_alignment/_subject_id_07-T2/registered_qT1.nii.gz
190331-00:25:34,208 nipype.utils DEBUG:
	 /Volumes/group/proc/TIGERanalysis/qT1/DataDir_qT1_FLUXRUN/1_check_alignment/_subject_id_07-T2/registered_qT1.nii.gz
190331-00:25:35,555 nipype.utils

190331-00:26:07,783 nipype.utils DEBUG:
	 Loading pkl: /Volumes/group/proc/TIGERanalysis/qT1/workflow_qT1_FLUXRUN/qt1proc_flow/_subject_id_06-T1/reorient/result_reorient.pklz
190331-00:26:07,851 nipype.workflow DEBUG:
	 output: out_file
190331-00:26:07,851 nipype.workflow DEBUG:
	 [Node] datasink - setting input 1_check_alignment.@par = /Volumes/group/proc/TIGERanalysis/qT1/workflow_qT1_FLUXRUN/qt1proc_flow/_subject_id_06-T1/reorient/reoriented_qT1.nii.gz
190331-00:26:07,852 nipype.workflow DEBUG:
	 input: 1_check_alignment.@par.@par
190331-00:26:07,853 nipype.workflow DEBUG:
	 results file: /Volumes/group/proc/TIGERanalysis/qT1/workflow_qT1_FLUXRUN/qt1proc_flow/_subject_id_06-T1/register_qt1/result_register_qt1.pklz
190331-00:26:07,853 nipype.utils DEBUG:
	 Loading pkl: /Volumes/group/proc/TIGERanalysis/qT1/workflow_qT1_FLUXRUN/qt1proc_flow/_subject_id_06-T1/register_qt1/result_register_qt1.pklz
190331-00:26:07,893 nipype.workflow DEBUG:
	 [Node] Writing post-exec report to "/Volumes/

190331-00:26:09,816 nipype.workflow DEBUG:
	 input: in_file
190331-00:26:09,817 nipype.workflow DEBUG:
	 results file: /Volumes/group/proc/TIGERanalysis/qT1/workflow_qT1_FLUXRUN/qt1proc_flow/_subject_id_02-T2/reorient/result_reorient.pklz
190331-00:26:09,817 nipype.utils DEBUG:
	 Loading pkl: /Volumes/group/proc/TIGERanalysis/qT1/workflow_qT1_FLUXRUN/qt1proc_flow/_subject_id_02-T2/reorient/result_reorient.pklz
190331-00:26:10,125 nipype.workflow DEBUG:
	 output: out_file
190331-00:26:10,126 nipype.workflow DEBUG:
	 [Node] register_qt1 - setting input in_file = /Volumes/group/proc/TIGERanalysis/qT1/workflow_qT1_FLUXRUN/qt1proc_flow/_subject_id_02-T2/reorient/reoriented_qT1.nii.gz
190331-00:26:10,235 nipype.workflow DEBUG:
	 [Node] Hashes: [('in_file', ('/Volumes/group/proc/TIGERanalysis/qT1/workflow_qT1_FLUXRUN/qt1proc_flow/_subject_id_02-T2/reorient/reoriented_qT1.nii.gz', '573a92dbe2ca1f233a76da8674a3c3bc')), ('out_file', 'registered_qT1.nii.gz'), ('out_matrix_file', 'flirt_transform_

	 Needed files: /Volumes/group/proc/TIGERanalysis/qT1/workflow_qT1_FLUXRUN/qt1proc_flow/_subject_id_02-T2/register_qt1/registered_qT1.nii.gz;/Volumes/group/proc/TIGERanalysis/qT1/workflow_qT1_FLUXRUN/qt1proc_flow/_subject_id_02-T2/register_qt1/flirt_transform_qt1.hdr;/Volumes/group/proc/TIGERanalysis/qT1/workflow_qT1_FLUXRUN/qt1proc_flow/_subject_id_02-T2/register_qt1/flirt_transform_qt1.img;/Volumes/group/proc/TIGERanalysis/qT1/workflow_qT1_FLUXRUN/qt1proc_flow/_subject_id_02-T2/register_qt1/flirt_transform_qt1.mat;/Volumes/group/proc/TIGERanalysis/qT1/workflow_qT1_FLUXRUN/qt1proc_flow/_subject_id_02-T2/register_qt1/flirt_transform_qt1.nii;/Volumes/group/proc/TIGERanalysis/qT1/workflow_qT1_FLUXRUN/qt1proc_flow/_subject_id_02-T2/register_qt1/flirt_transform_qt1.mat;/Volumes/group/proc/TIGERanalysis/qT1/workflow_qT1_FLUXRUN/qt1proc_flow/_subject_id_02-T2/reorient/reoriented_qT1.nii.gz;/Volumes/group/proc/TIGERanalysis/qT1/workflow_qT1_FLUXRUN/qt1proc_flow/_subject_id_02-T2/stripT1/T1_ac

	 Copying File: /Volumes/group/proc/TIGERanalysis/qT1/DataDir_qT1_FLUXRUN/1_check_alignment/_subject_id_02-T2/registered_qT1.nii.gz->/Volumes/group/proc/TIGERanalysis/qT1/workflow_qT1_FLUXRUN/qt1proc_flow/_subject_id_02-T2/register_qt1/registered_qT1.nii.gz
190331-00:27:10,957 nipype.utils DEBUG:
	 /Volumes/group/proc/TIGERanalysis/qT1/DataDir_qT1_FLUXRUN/1_check_alignment/_subject_id_02-T2/registered_qT1.nii.gz
190331-00:27:11,844 nipype.utils DEBUG:
	 File: /Volumes/group/proc/TIGERanalysis/qT1/DataDir_qT1_FLUXRUN/1_check_alignment/_subject_id_02-T2/registered_qT1.nii.gz already exists,09dff37dee80e512a12f81bc43f858bc, copy:1
190331-00:27:12,559 nipype.utils DEBUG:
	 File: /Volumes/group/proc/TIGERanalysis/qT1/DataDir_qT1_FLUXRUN/1_check_alignment/_subject_id_02-T2/registered_qT1.nii.gz already exists, not overwriting, copy:1
190331-00:27:13,67 nipype.workflow DEBUG:
	 Needed files: /Volumes/group/proc/TIGERanalysis/qT1/DataDir_qT1_FLUXRUN/1_check_alignment/_subject_id_02-T2/T1_acpc_

In [16]:
#SelectFiles
template2 = dict(qt1r=data_dir+'/1_check_alignment/_subject_id_{subject_id}/registered_qT1.nii.gz',
               unc_maskL = fpath+'/{subject_id}/Left_Uncinate.nii.gz',
               unc_maskR = fpath+'/{subject_id}/Right_Uncinate.nii.gz',
               cc_maskL = fpath+'/{subject_id}/Left_Cingulum_Cingulate.nii.gz',
               cc_maskR = fpath+'/{subject_id}/Right_Cingulum_Cingulate.nii.gz')

# 
#             bval=fpath+'/{subject_id}/dti.bval',
#             bvec=fpath+'/{subject_id}/dti.bvec'

sf2 = Node(SelectFiles(template2, 
                      base_directory = fpath),
          name = 'sf2')

In [17]:
get_stats=Workflow(name='get_stats')
get_stats.connect([(infosource, sf2, [('subject_id','subject_id')]),
                   (sf2, get_voxLUF, [('qt1r', 'in_file')]),
                   (sf2, get_voxLUF, [('unc_maskL', 'mask')]),
                   (get_voxLUF, datasink, [('out_file', '2_Extracted_Stats')]),
                   (sf2, get_voxLCC, [('qt1r', 'in_file')]),
                   (sf2, get_voxLCC, [('cc_maskL', 'mask')]),
                   (get_voxLCC, datasink, [('out_file', '2_Extracted_Stats.@par')]),
                   (sf2, get_voxRUF, [('qt1r', 'in_file')]),
                   (sf2, get_voxRUF, [('unc_maskR', 'mask')]),
                   (get_voxRUF, datasink, [('out_file', '2_Extracted_Stats.@par.@par')]),
                   (sf2, get_voxRCC, [('qt1r', 'in_file')]),
                   (sf2, get_voxRCC, [('cc_maskR', 'mask')]),
                   (get_voxRCC, datasink, [('out_file', '2_Extracted_Stats.@par.@par.@par')])
                  ])
get_stats.base_dir = workflow_dir
get_stats.write_graph(graph2use = 'flat')
preproc = get_stats.run('MultiProc', plugin_args={'n_procs': 4})

190331-00:28:36,596 nipype.workflow DEBUG:
	 (qt1proc_flow.infosource, get_stats.sf2): No edge data
190331-00:28:36,597 nipype.workflow DEBUG:
	 (qt1proc_flow.infosource, get_stats.sf2): new edge data: {'connect': [('subject_id', 'subject_id')]}
190331-00:28:36,598 nipype.workflow DEBUG:
	 (get_stats.sf2, get_stats.get_voxLUF): No edge data
190331-00:28:36,598 nipype.workflow DEBUG:
	 (get_stats.sf2, get_stats.get_voxLUF): new edge data: {'connect': [('qt1r', 'in_file')]}
190331-00:28:36,599 nipype.workflow DEBUG:
	 (get_stats.sf2, get_stats.get_voxLUF): Edge data exists: {'connect': [('qt1r', 'in_file')]}
190331-00:28:36,600 nipype.workflow DEBUG:
	 (get_stats.sf2, get_stats.get_voxLUF): new edge data: {'connect': [('qt1r', 'in_file'), ('unc_maskL', 'mask')]}
190331-00:28:36,601 nipype.workflow DEBUG:
	 (get_stats.get_voxLUF, qt1proc_flow.datasink): No edge data
190331-00:28:36,602 nipype.workflow DEBUG:
	 (get_stats.get_voxLUF, qt1proc_flow.datasink): new edge data: {'connect': [('ou

190331-00:28:39,183 nipype.workflow DEBUG:
	 Parameterization: paramstr=_subject_id_15-T1
190331-00:28:39,186 nipype.workflow DEBUG:
	 [Node] infosource - setting input subject_id = 16-T1
190331-00:28:39,187 nipype.workflow DEBUG:
	 Parameterization: paramstr=_subject_id_16-T1
190331-00:28:39,190 nipype.workflow DEBUG:
	 [Node] infosource - setting input subject_id = 17-T1
190331-00:28:39,191 nipype.workflow DEBUG:
	 Parameterization: paramstr=_subject_id_17-T1
190331-00:28:39,194 nipype.workflow DEBUG:
	 [Node] infosource - setting input subject_id = 18-T1
190331-00:28:39,195 nipype.workflow DEBUG:
	 Parameterization: paramstr=_subject_id_18-T1
190331-00:28:39,198 nipype.workflow DEBUG:
	 [Node] infosource - setting input subject_id = 19-T1
190331-00:28:39,199 nipype.workflow DEBUG:
	 Parameterization: paramstr=_subject_id_19-T1
190331-00:28:39,202 nipype.workflow DEBUG:
	 [Node] infosource - setting input subject_id = 20-T1
190331-00:28:39,203 nipype.workflow DEBUG:
	 Parameterizatio

190331-00:28:39,304 nipype.workflow DEBUG:
	 [Node] sf2 - setting input subject_id = 35-T1
190331-00:28:39,304 nipype.workflow DEBUG:
	 Removed the identity node qt1proc_flow.infosource from the graph.
190331-00:28:39,305 nipype.workflow DEBUG:
	 [Node] sf2 - setting input subject_id = 32-T1
190331-00:28:39,305 nipype.workflow DEBUG:
	 Removed the identity node qt1proc_flow.infosource from the graph.
190331-00:28:39,305 nipype.workflow DEBUG:
	 [Node] sf2 - setting input subject_id = 31-T1
190331-00:28:39,306 nipype.workflow DEBUG:
	 Removed the identity node qt1proc_flow.infosource from the graph.
190331-00:28:39,306 nipype.workflow DEBUG:
	 [Node] sf2 - setting input subject_id = 30-T1
190331-00:28:39,307 nipype.workflow DEBUG:
	 Removed the identity node qt1proc_flow.infosource from the graph.
190331-00:28:39,307 nipype.workflow DEBUG:
	 [Node] sf2 - setting input subject_id = 29-T1
190331-00:28:39,308 nipype.workflow DEBUG:
	 Removed the identity node qt1proc_flow.infosource from t

190331-00:28:44,125 nipype.workflow DEBUG:
	 Setting node inputs
190331-00:28:44,126 nipype.workflow INFO:
	 [Node] Setting-up "get_stats.sf2" in "/Volumes/group/proc/TIGERanalysis/qT1/workflow_qT1_FLUXRUN/get_stats/_subject_id_109-T1/sf2".
190331-00:28:44,136 nipype.utils DEBUG:
	 Creating directory /Volumes/group/proc/TIGERanalysis/qT1/workflow_qT1_FLUXRUN/get_stats/_subject_id_110-T1/sf2190331-00:28:44,136 nipype.workflow DEBUG:
	 [Node] Directory not found "/Volumes/group/proc/TIGERanalysis/qT1/workflow_qT1_FLUXRUN/get_stats/_subject_id_109-T1/sf2".

190331-00:28:44,140 nipype.utils DEBUG:
	 Removing contents of /Volumes/group/proc/TIGERanalysis/qT1/workflow_qT1_FLUXRUN/get_stats/_subject_id_109-T1/sf2
190331-00:28:44,173 nipype.workflow DEBUG:
	 [Node] Directory not found "/Volumes/group/proc/TIGERanalysis/qT1/workflow_qT1_FLUXRUN/get_stats/_subject_id_108-T1/sf2".
190331-00:28:44,174 nipype.workflow DEBUG:
	 Checking hash "get_stats.sf2" locally: cached=False, updated=False.
1903

190331-00:28:52,256 nipype.workflow DEBUG:
	 [Node] get_voxRCC - setting input mask = /Volumes/group/proc/TIGERanalysis/qT1/subjDir/111-T1/Right_Cingulum_Cingulate.nii.gz
190331-00:28:52,309 nipype.workflow DEBUG:
	 [Node] Directory not found "/Volumes/group/proc/TIGERanalysis/qT1/workflow_qT1_FLUXRUN/get_stats/_subject_id_111-T1/get_voxRCC".
190331-00:28:52,310 nipype.workflow DEBUG:
	 Checking hash "get_stats.get_voxRCC" locally: cached=False, updated=False.
190331-00:28:52,312 nipype.workflow DEBUG:
	 [MultiProc] Submitted task get_stats.get_voxRCC (taskid=5).
190331-00:28:52,313 nipype.workflow DEBUG:
	 Allocating get_stats.get_voxRUF ID=2 (0.20GB, 1 threads). Free: 28.20GB, 1 threads.
190331-00:28:52,313 nipype.workflow DEBUG:
	 Setting node inputs
190331-00:28:52,314 nipype.workflow DEBUG:
	 input: in_file
190331-00:28:52,315 nipype.workflow DEBUG:
	 results file: /Volumes/group/proc/TIGERanalysis/qT1/workflow_qT1_FLUXRUN/get_stats/_subject_id_111-T1/sf2/result_sf2.pklz
190331-00

...

190331-00:42:50,15 nipype.workflow DEBUG:
	 results file: /Volumes/group/proc/TIGERanalysis/qT1/workflow_qT1_FLUXRUN/get_stats/_subject_id_06-T1/get_voxLCC/result_get_voxLCC.pklz
190331-00:42:50,15 nipype.utils DEBUG:
	 Loading pkl: /Volumes/group/proc/TIGERanalysis/qT1/workflow_qT1_FLUXRUN/get_stats/_subject_id_06-T1/get_voxLCC/result_get_voxLCC.pklz
190331-00:42:49,548 nipype.utils DEBUG:
	 File: /Volumes/group/proc/TIGERanalysis/qT1/DataDir_qT1_FLUXRUN/2_Extracted_Stats/_subject_id_07-T2/ROI_voxel-contrasts_LeftCC.txt already exists,289a0534f24c2831c74e5880db7e8912, copy:1190331-00:42:49,876 nipype.interface DEBUG:
	 in_file_/Volumes/group/proc/TIGERanalysis/qT1/DataDir_qT1_FLUXRUN/1_check_alignment/_subject_id_02-T2/registered_qT1.nii.gz

190331-00:42:50,573 nipype.interface DEBUG:
	 mask_/Volumes/group/proc/TIGERanalysis/qT1/subjDir/02-T2/Right_Cingulum_Cingulate.nii.gz
190331-00:42:50,578 nipype.interface DEBUG:
	 order_1
190331-00:42:50,582 nipype.interface DEBUG:
	 out_file_ROI

	 Copying File: /Volumes/group/proc/TIGERanalysis/qT1/DataDir_qT1_FLUXRUN/2_Extracted_Stats/_subject_id_07-T2/ROI_voxel-contrasts_RightCC.txt->/Volumes/group/proc/TIGERanalysis/qT1/workflow_qT1_FLUXRUN/get_stats/_subject_id_07-T2/get_voxRCC/ROI_voxel-contrasts_RightCC.txt
190331-00:42:54,643 nipype.workflow DEBUG:
	 No resources available
190331-00:42:54,847 nipype.utils DEBUG:
	 Creating directory /Volumes/group/proc/TIGERanalysis/qT1/workflow_qT1_FLUXRUN/qt1proc_flow/_subject_id_06-T1/datasink/_report
190331-00:42:55,62 nipype.utils DEBUG:
	 /Volumes/group/proc/TIGERanalysis/qT1/DataDir_qT1_FLUXRUN/2_Extracted_Stats/_subject_id_07-T2/ROI_voxel-contrasts_RightCC.txt
190331-00:42:55,88 nipype.workflow DEBUG:
	 [Node] Writing pre-exec report to "/Volumes/group/proc/TIGERanalysis/qT1/workflow_qT1_FLUXRUN/qt1proc_flow/_subject_id_06-T1/datasink/_report/report.rst"
190331-00:42:55,297 nipype.utils DEBUG:
	 File: /Volumes/group/proc/TIGERanalysis/qT1/DataDir_qT1_FLUXRUN/2_Extracted_Stats/_s

	 copyfile: /Volumes/group/proc/TIGERanalysis/qT1/workflow_qT1_FLUXRUN/get_stats/_subject_id_06-T1/get_voxRUF/ROI_voxel-contrasts_RightUncinate.txt /Volumes/group/proc/TIGERanalysis/qT1/DataDir_qT1_FLUXRUN/2_Extracted_Stats/_subject_id_06-T1/ROI_voxel-contrasts_RightUncinate.txt
190331-00:43:03,946 nipype.utils DEBUG:
	 /Volumes/group/proc/TIGERanalysis/qT1/DataDir_qT1_FLUXRUN/2_Extracted_Stats/_subject_id_06-T1/ROI_voxel-contrasts_RightUncinate.txt
190331-00:43:04,178 nipype.workflow INFO:
	 [Node] Running "get_voxLCC" ("nipype.interfaces.fsl.utils.ImageMeants"), a CommandLine Interface with command:
fslmeants -i /Volumes/group/proc/TIGERanalysis/qT1/DataDir_qT1_FLUXRUN/1_check_alignment/_subject_id_02-T2/registered_qT1.nii.gz -m /Volumes/group/proc/TIGERanalysis/qT1/subjDir/02-T2/Left_Cingulum_Cingulate.nii.gz --order=1 -o ROI_voxel-contrasts_LeftCC.txt --showall190331-00:43:03,967 nipype.utils DEBUG:
	 Linking File: /Volumes/group/proc/TIGERanalysis/qT1/DataDir_qT1_FLUXRUN/2_Extract

190331-00:43:12,680 nipype.workflow INFO:
	 [MultiProc] Running 1 tasks, and 0 jobs ready. Free memory (GB): 28.60/28.80, Free processors: 3/4.
                     Currently running:
                       * get_stats.get_voxLUF
190331-00:43:13,233 nipype.workflow INFO:
	 [Node] Finished "get_stats.get_voxLUF".
190331-00:43:14,676 nipype.workflow DEBUG:
	 Progress: 228 jobs, 226/1/0 (done/running/ready), 1/1 (pending_tasks/waiting).
190331-00:43:14,677 nipype.workflow INFO:
	 [Job 226] Completed (get_stats.get_voxLUF).
190331-00:43:14,679 nipype.workflow DEBUG:
	 Tasks currently running: 0. Pending: 0.
190331-00:43:14,681 nipype.workflow INFO:
	 [MultiProc] Running 0 tasks, and 1 jobs ready. Free memory (GB): 28.80/28.80, Free processors: 4/4.
190331-00:43:14,717 nipype.workflow DEBUG:
	 Allocating qt1proc_flow.datasink ID=227 (0.20GB, 1 threads). Free: 28.60GB, 3 threads.
190331-00:43:14,717 nipype.workflow DEBUG:
	 Setting node inputs
190331-00:43:14,718 nipype.workflow DEBUG:
	 inp

	 key: 2_Extracted_Stats.@par.@par files: /Volumes/group/proc/TIGERanalysis/qT1/workflow_qT1_FLUXRUN/get_stats/_subject_id_02-T2/get_voxRUF/ROI_voxel-contrasts_RightUncinate.txt
190331-00:43:22,240 nipype.interface DEBUG:
	 copyfile: /Volumes/group/proc/TIGERanalysis/qT1/workflow_qT1_FLUXRUN/get_stats/_subject_id_02-T2/get_voxRUF/ROI_voxel-contrasts_RightUncinate.txt /Volumes/group/proc/TIGERanalysis/qT1/DataDir_qT1_FLUXRUN/2_Extracted_Stats/_subject_id_02-T2/ROI_voxel-contrasts_RightUncinate.txt
190331-00:43:22,244 nipype.utils DEBUG:
	 /Volumes/group/proc/TIGERanalysis/qT1/DataDir_qT1_FLUXRUN/2_Extracted_Stats/_subject_id_02-T2/ROI_voxel-contrasts_RightUncinate.txt
190331-00:43:22,265 nipype.utils DEBUG:
	 Linking File: /Volumes/group/proc/TIGERanalysis/qT1/DataDir_qT1_FLUXRUN/2_Extracted_Stats/_subject_id_02-T2/ROI_voxel-contrasts_RightUncinate.txt->/Volumes/group/proc/TIGERanalysis/qT1/workflow_qT1_FLUXRUN/get_stats/_subject_id_02-T2/get_voxRUF/ROI_voxel-contrasts_RightUncinate.txt